# Getting familiar with the MPS 

In [ ]:
import numpy as np
import tnsbasic
import matplotlib
from tnsbasic.mps import MPS,MPO
import tnsbasic.contractor as contractor

## Creating a MPS

[Creating and inspecting an MPS](#creating-and-inspecting-an-MPS)

The accompanying files provide basic MPS functionality.

*Note: the tensors in the MPS have indices ordered in the sequence `(physical, left, right)`.*

We create an empty MPS with
```python
MPS()
```

We can initialize the contents of the tensors in several ways:
 1. Random components 
 ```python
MPS.initializeRandom(N,d,D)
```
where
- `N` is the number of sites,
- `d` is the (uniform) physical dimension of the tensors, and
- `D` the maximal bond dimension.
In this case all tensors have the same physical dimension, and the bond dimensions are at most `D`, but they grow from the edges.
We can also initialize a MPS with all tensors of shape `(d,D,D)` (except for the first and the last one) with
```python
MPS.initializeRandomNoShape(N,d,D)
```

 2. A product state, providing a list of vectors. Each element of the list is interpreted as a vector, and its number of components sets the physical dimension of the corresponding site. The length is determined to be the number of terms in the list.
  ```python
MPS.initializeProductState(vector_list)
```

To inspect the result, we can use the method ```getBondDimensions()```, which returns a list with the dimensions of all the bonds in the MPS. For more details, ```printMPS()``` prints the shapes of all the tensors (including lambda matrices, potentially). The explicit tensors for one site are shown by `printSite(pos)`.


See the following examples.


In [ ]:
# Create a random MPS of given length and bond dimension

N=7; 
d=2;
D=14;

anMPS=MPS();#N,d,D); # this just creates an empty MPS
print('After initialization, length=',anMPS.length(),'bond dimensions',anMPS.getBondDimensions());

anMPS.initializeRandomNoShape(N,d,D); # now it should be full of random (complex) components

# Let's check the bond dimensions
Ds=anMPS.getBondDimensions();
print('Initialized random MPS with length',anMPS.length(),' and bond dimensions: ',Ds);

anMPS.initializeRandom(N,d,D); # now it should be full of random (complex) components

# Let's check the bond dimensions
Ds=anMPS.getBondDimensions();
print('Initialized random MPS with length',anMPS.length(),' and bond dimensions: ',Ds);


# Or initialize as a product
prodMPS=MPS();#N,d,D); # this just creates an empty MPS
prodMPS.initializeProductState([np.array([1.,0.])]*N); # now it should be full of random (complex) components

# Let's check the bond dimensions
Ds=prodMPS.getBondDimensions();
print('Initialized product state MPS with length',anMPS.length(),' and bond dimensions: ',Ds);

# We can also print out all the MPS shapes, which are ordered as d x Dl x Dr
# anMPS.printMPS();
# Or print out tensor(s) for one site, with all components
# pos=5;
# anMPS.printSite(pos);


## Gauge conditions

[Gauge conditions](#gauge-conditions)

We can impose a gauge condition (left, right mixed or canonical) using the following method.

```python
gaugeCondition(mode,normalize=False,site=None)
```
where
 - `mode` can be one of the following strings:
         'l' 'L' -> left normalized
         'r' 'R' -> left normalized
         'lr' 'LR' 'mixed' 'centered' -> mixed (requires third argument site to be a valid position 
                                         in the MPS [0,N-1])
         'canonical' 'can' -> full canonical form (lambdas)
 - `normalize=True` means that the MPS ends up normalized; otherwise, there is a norm factor different from one 
         (while tensors are still in the appropriate gauge)
         
Whether a gauge condition has been immposed of not, a MPS can have an overall norm factor, which can be recovered using the method `MPS.getNormFactor()`.    

To check whether gauge conditions are fulfilled, we can invoke the following methods:

- `checkGauge()` -> for each site in the chain computes and shows how much the gauge conditions are violated: $\|\sum_i {A^i}^{\dagger} A^i - \mathbb{1}_{Dr}\|$ (gauge L) and $\|\sum_i A^i {A^i}^{\dagger}  - \mathbb{1}_{Dl}\|$ (gauge R).

- `checkCanonical()` -> for each site in the chain computes and shows how much the orthogonality condition are violated: $\|\sum_i {A^i}^{\dagger} \lambda_{i-1} A^i - \mathbb{1}_{Dr}\|$ (gauge L) and $\|\sum_i A^i \lambda_{i} {A^i}^{\dagger}  - \mathbb{1}_{Dl}\|$ (gauge R) (if the lambda matrices are not explicit, e.g. if gauge condition 'L' was imposed, it is equivalent to the previous one).

- `checkBondOrthogonality()`  -> checks for each site the orthogonality, contracting explicitly all tensors to the left (orth L) or to the right (orth R)

In [ ]:
# Before imposing the gauge, check explicitly
anMPS.initializeRandomNoShape(N,d,D); 
Ds=anMPS.getBondDimensions();
print('Initialized random MPS with length',anMPS.length(),' and bond dimensions: ',Ds);

print('\nAfter initialization:\n=== ');
anMPS.checkGauge();

# Impose a gauge condition and check again
gauge='L'; # could be 'R','LR','canonical',...
print('\nImposing the gauge {0}: '.format(gauge));
anMPS.gaugeCondition(gauge);
anMPS.gaugeCondition('LR',site=3);
print('\t now dimensions:',anMPS.getBondDimensions(),'\n===');
anMPS.checkGauge();

# Other conditons can be checked:
#anMPS.gaugeCondition('r',1);
#anMPS.gaugeCondition('mixed',True,2);

# Checking that the norm did not change (if not normalized)
print('<MPS|MPS>=',contractor.contractBraKet(anMPS,anMPS));


## Contracting MPS

[Contractions](#contractions)

The module `tnsbasic.contractor` provides basic routines to contract MPS:

```
contractor.contractBraKet(bra,ket)
```
computes the braket contraction of the arguments, where `bra`and `ket` have to be `MPS` objects of the same length. Notice that `bra` should not be conjugated by hand (it is done by the method). The result is, in general, complex.

```
contractor.localExpectationValue(state,operator,pos)
``` 
computes the expectation value with respect to the MPS `state` of a single site `operator` acting on site `pos`.

```
contractor.multiLocalExpectationValue(state,operators,sites)
```
similar to the previous method, computes the expectation value of the tensor product of a list `operators` of single site operators acting on the list of `sites`.


In [ ]:
# The norm is obtained contracting the MPS with itself
normSt=contractor.contractBraKet(anMPS,anMPS);
print('<MPS|MPS>=',normSt);

# Or we can contract wiht a different state, e.g. with the product state above
print('<prodMPS|MPS>=',contractor.contractBraKet(prodMPS,anMPS));

anMPS.initializeRandomNoShape(N,d,D);
# We can check that imposing the canonical form does not change results, except for the normalization
anMPS.canonicalForm(); # Equivalent to gaugeCondition('canonical',1);

anMPS.checkCanonical();
anMPS.checkGauge();
anMPS.checkBondOrthogonality();
# Checking that the norm did not change (if not normalized)
print('After canonical form <MPS|MPS>=',contractor.contractBraKet(anMPS,anMPS));
print('\t and <prodMPS|MPS>=',contractor.contractBraKet(prodMPS,anMPS));
print('\t Norm*<prodMPS|MPS>=',np.sqrt(normSt)*contractor.contractBraKet(prodMPS,anMPS));


### Expectation values
[Computing observables](#computing-observables)

In [ ]:
# Try computing an expectation value for a single site operator

# Pauli matrices
sigmaX=np.array([[0,1.],[1.,0]]);
sigmaY=np.array([[0,-1j],[1j,0]]);
sigmaZ=np.array([[1.,0],[0,-1.]]);

# 1) Create a single site operator (e.g. one Pauli)
localOp=sigmaX;

# The operator could be (e.g. random 2x2 Hermitian matrix)
randomO=np.random.rand(d,d)*np.exp(1j*2*np.pi*np.random.rand(d,d));
randomO=.5*(randomO+np.transpose(np.conj(randomO)));
#localOp=randomO;

# 2) Compute its expectation value in our MPS state
pos=3;
expV=contractor.localExpectationValue(anMPS,localOp,pos);
print('Expectation value of localOp on position {0} is {1}'.format(pos,np.real(expV)));

# Show e.v. for each site 
allExpV=[[pos,np.real(contractor.localExpectationValue(anMPS,localOp,pos))] for pos in range(N)];
print(allExpV)

In [ ]:
# Try a two body expectation value
opers=[sigmaZ,sigmaZ];
sites=[2,5];

expV=contractor.multiLocalExpectationValue(anMPS,opers,sites);
print(expV)


# Show e.v. for each pair including site 2 
allExpV=[np.real(contractor.multiLocalExpectationValue(anMPS,opers,[2,pos])) for pos in range(3,N)];
print(allExpV)

### Computing the entropy

With the functions described so far and the gauge forms, it is easy to determine the entanglement entropy with respect to cutting any bond in a `MPS`.
 1. We could use a mixed gauge, centered around the interesting bond.
 2. We can ensure first the canonical form and simply read the Schmidt values as demonstrated below.

In [ ]:
# Compute entropy corresponding to the bipartition obtained by cutting one bond.
cut=2; # from 0 to N-1

anMPS.canonicalForm(1);
print('Schmidt values for cut %d'%cut,np.real(anMPS.lambdas[cut])); # these are the Schmidt values 
entrC=-2*np.real(np.sum(anMPS.lambdas[cut]**2*np.log(anMPS.lambdas[cut]))); # actually should take care of zero values
print('S(%d)=%g'%(cut,entrC))

### Saving and reading

The code provides also basic functions to save and load a `MPS` to or from a file. 

In [ ]:
# Test save and load methods
mpsfile='testMPSfile.npz';
rndMPS=MPS();
rndMPS.initializeRandom(N,d,D);
print(np.real(contractor.contractBraKet(rndMPS,anMPS)));
anMPS.save(mpsfile);
anotherMPS=MPS();
anotherMPS.load(mpsfile);
anotherMPS.printMPS();
print(np.real(contractor.contractBraKet(rndMPS,anotherMPS)));


## Additional exercises

Create a random MPS of length at least 100. 

 1. Find and plot the Schmidt values for the middle cut. 

 2. Compute the connected two-point correlations $$\langle \sigma_z^{[i]} \sigma_z^{[i+x]} \rangle- \langle \sigma_z^{[i]}\rangle \langle \sigma_z^{[i+x]} \rangle$$ for $i=N/4$ and $1\leq x\leq 3N/4$. Plot as a function of the distance $x$. 

 3. Compute the entropy of a single site in the center of the chain.
 
 4. How can we compute the entropy of a subchain in the middle of the system? (e.g. the 10 sites in the center). Is it efficient?